In [1]:
# Dependencies and Setup
import pandas as pd
import numpy as np
import requests
import gmaps
import os
import json
from scipy.stats import linregress
from config import api_key
from config import g_key
from census import Census
c = Census(api_key, year=2013)

# File to Load (Unclean member file)
file_to_load = "active_lapsed.csv"

# Read unclean member file and store into Pandas data frame
member_data = pd.read_csv(file_to_load)
member_data.head()

from sqlalchemy import create_engine

In [2]:
# Define DataFrame for member file
member_data_df = pd.DataFrame(member_data)

In [3]:
# Blurred address column for protection
def blurry(s):
    return 'color: transparent; text-shadow: 0 0 5px rgba(0,0,0,0.5)'

In [4]:
# Blur data for privacy
member_data_df.style.applymap(blurry, subset=['Address'])

In [5]:
# Total count of UNIQUE member addresses
number_of_rows = len(member_data_df['Address'].unique())
number_of_rows

1340

In [6]:
# Rename Zip Code to Zipcode and Blur Data for Privacy
member_data_df = member_data_df.rename(columns={'Zip_Code':'Zipcode'})

member_data_df.style.applymap(blurry, subset=['Address'])

In [7]:
# Total count of addresses (including duplicates)
qty_of_addresses = len(member_data_df['Address'])
qty_of_addresses

1890

In [8]:
revised_member_df = member_data_df.drop_duplicates(subset='Address', keep="first")
revised_member_df

revised_member_df.style.applymap(blurry, subset=['Address'])

In [9]:
# Remove last 4-digits of zip code
revised_member_df['Zipcode'] = revised_member_df['Zipcode'].where(revised_member_df['Zipcode'].str.len() == 5, 
                                               revised_member_df['Zipcode'].str[:5])

<ipython-input-9-b3fc12698fb7>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  revised_member_df['Zipcode'] = revised_member_df['Zipcode'].where(revised_member_df['Zipcode'].str.len() == 5,


In [10]:
revised_member_df.head()
revised_member_df.style.applymap(blurry, subset=['Address'])

In [11]:
# Checking type of zip code
type('Zipcode')

str

In [12]:
# Retrieving second file via API
# Run Census Search to retrieve data on all zip codes (2013 ACS5 Census)
# See: https://github.com/CommerceDataService/census-wrapper for library documentation
# See: https://gist.github.com/afhaque/60558290d6efd892351c4b64e5c01e9b for labels
census_data = c.acs5.get(("NAME", "B19013_001E", "B01003_001E", "B01002_001E",
                          "B19301_001E",
                          "B17001_002E"), {'for': 'zip code tabulation area:*'})
# Convert to DataFrame
census_pd = pd.DataFrame(census_data)
# Column Reordering
census_pd = census_pd.rename(columns={"B01003_001E": "Population",
                                      "B01002_001E": "Median Age",
                                      "B19013_001E": "Household Income",
                                      "B19301_001E": "Per Capita Income",
                                      "B17001_002E": "Poverty Count",
                                      "NAME": "Name", "zip code tabulation area": "Zipcode"})
# Add in Poverty Rate (Poverty Count / Population)
census_pd["Poverty Rate"] = 100 * \
    census_pd["Poverty Count"].astype(
        int) / census_pd["Population"].astype(int)
# Final DataFrame
census_pd = census_pd[["Zipcode", "Population", "Median Age", "Household Income",
                       "Per Capita Income", "Poverty Count", "Poverty Rate"]]
# Visualize
print(len(census_pd))
census_pd.head()

33120


Zipcode  Population  Median Age  Household Income  Per Capita Income  \
0   08518      5217.0        41.5           74286.0            33963.0   
1   08520     27468.0        37.4           90293.0            37175.0   
2   08525      4782.0        47.1          118656.0            59848.0   
3   08527     54867.0        42.2           88588.0            37021.0   
4   08528       245.0        48.5           58676.0            49117.0   

   Poverty Count  Poverty Rate  
0          170.0      3.258578  
1         1834.0      6.676860  
2           43.0      0.899205  
3         2191.0      3.993293  
4            0.0      0.000000

In [13]:
# Convert to DataFrame
census_pd = pd.DataFrame(census_data)
# Column Reordering
census_pd = census_pd.rename(columns={"B01003_001E": "Population",
                                      "B01002_001E": "Median Age",
                                      "B19013_001E": "Household Income",
                                      "B19301_001E": "Per Capita Income",
                                      "B17001_002E": "Poverty Count",
                                      "NAME": "Name", "zip code tabulation area": "Zipcode"})
# Add in Poverty Rate (Poverty Count / Population)
census_pd["Poverty Rate"] = 100 * \
    census_pd["Poverty Count"].astype(
        int) / census_pd["Population"].astype(int)
# Final DataFrame
census_pd = census_pd[["Zipcode", "Population", "Median Age", "Household Income",
                       "Per Capita Income", "Poverty Count", "Poverty Rate"]]
# Visualize
print(len(census_pd))
census_pd.head()

33120


Zipcode  Population  Median Age  Household Income  Per Capita Income  \
0   08518      5217.0        41.5           74286.0            33963.0   
1   08520     27468.0        37.4           90293.0            37175.0   
2   08525      4782.0        47.1          118656.0            59848.0   
3   08527     54867.0        42.2           88588.0            37021.0   
4   08528       245.0        48.5           58676.0            49117.0   

   Poverty Count  Poverty Rate  
0          170.0      3.258578  
1         1834.0      6.676860  
2           43.0      0.899205  
3         2191.0      3.993293  
4            0.0      0.000000

In [14]:
# Check zipcode type
type('Zipcode')

str

In [15]:
# Merge data sets

merge_df = pd.merge(census_pd, revised_member_df, how = 'outer', on ='Zipcode')
merge_df

Zipcode  Population  Median Age  Household Income  Per Capita Income  \
0       08518      5217.0        41.5           74286.0            33963.0   
1       08520     27468.0        37.4           90293.0            37175.0   
2       08525      4782.0        47.1          118656.0            59848.0   
3       08527     54867.0        42.2           88588.0            37021.0   
4       08528       245.0        48.5           58676.0            49117.0   
...       ...         ...         ...               ...                ...   
34206   33222         NaN         NaN               NaN                NaN   
34207   33234         NaN         NaN               NaN                NaN   
34208   33239         NaN         NaN               NaN                NaN   
34209   70184         NaN         NaN               NaN                NaN   
34210   33171         NaN         NaN               NaN                NaN   

       Poverty Count  Poverty Rate     Member Level  Status Expiration Date  \
0              170.0      3.258578              NaN     NaN             NaN   
1             1834.0      6.676860              NaN     NaN             NaN   
2               43.0      0.899205              NaN     NaN             NaN   
3             2191.0      3.993293              NaN     NaN             NaN   
4                0.0      0.000000              NaN     NaN             NaN   
...              ...           ...              ...     ...             ...   
34206            NaN           NaN  Dual Membership  Active         2/28/21   
34207            NaN           NaN  Dual Membership  Active        10/31/22   
34208            NaN           NaN  Dual Membership  Active         4/30/21   
34209            NaN           NaN  Dual Membership  Active         4/30/21   
34210            NaN           NaN  Dual Membership  Active        10/31/21   

               Address          City      State  
0                  NaN           NaN        NaN  
1                  NaN           NaN        NaN  
2                  NaN           NaN        NaN  
3                  NaN           NaN        NaN  
4                  NaN           NaN        NaN  
...                ...           ...        ...  
34206    PO Box 227814         Miami    Florida  
34207    PO Box 348254  Coral Gables    Florida  
34208    PO Box 398522   Miami Beach    Florida  
34209     PO Box 24655   New Orleans  Louisiana  
34210  815 83rd Street   Miami Beach    Florida  

[34211 rows x 13 columns]

In [16]:
# Remove null rows
merge_df = merge_df.dropna()
merge_df

Zipcode  Population  Median Age  Household Income  Per Capita Income  \
10      08540     47316.0        37.5          125439.0            61810.0   
120     10001     21966.0        34.7           81671.0            82166.0   
121     10002     82191.0        39.8           33218.0            26227.0   
129     10011     52167.0        39.7          104238.0           110631.0   
139     10022     29618.0        45.3          109019.0           129778.0   
...       ...         ...         ...               ...                ...   
31386   91789     42609.0        42.5           91623.0            33534.0   
31387   91789     42609.0        42.5           91623.0            33534.0   
31478   92119     22965.0        43.1           67616.0            34648.0   
31815   78577     72047.0        28.6           32054.0            12969.0   
32871   96734     53068.0        34.7           89016.0            36481.0   

       Poverty Count  Poverty Rate           Member Level  Status  \
10            1969.0      4.161383      Family Membership  Active   
120           3375.0     15.364654        Dual Membership  Active   
121          23346.0     28.404570        Dual Membership  Active   
129           4379.0      8.394196        Dual Membership  Active   
139           1318.0      4.449997        Dual Membership  Active   
...              ...           ...                    ...     ...   
31386         2448.0      5.745265        Dual Membership  Active   
31387         2448.0      5.745265        Dual Membership  Active   
31478         1638.0      7.132593  Individual Membership  Active   
31815        25856.0     35.887684      Family Membership  Active   
32871         3560.0      6.708374  Individual Membership  Active   

      Expiration Date                     Address       City       State  
10            4/30/21               52 Arreton Rd  Princeton  New Jersey  
120          11/30/21   100 W 27th street, Apt 2N   New York    New York  
121           2/28/21     215 Chrystie St Apt 29W   New York    New York  
129          12/31/20        415 W 24th St Apt 3A   New York    New York  
139           4/30/21        141 E 55th St Apt 9G   New York    New York  
...               ...                         ...        ...         ...  
31386        11/30/21             340 S Lemon Ave     Walnut  California  
31387        11/30/21  340 S Lemon Ave, unit 6133     Walnut  California  
31478         3/31/21        6335 Lake Lucerne Dr  San Diego  California  
31815         3/31/21                 PO Box 1330      Pharr       Texas  
32871         6/30/21          1254 Ulupii Street     Kailua      Hawaii  

[1321 rows x 13 columns]

In [17]:
# Isolate data to zipcode, median age, household income, member level, status, expiration date,  city, state
merge_df = merge_df.drop(columns=['Per Capita Income', 'Poverty Count', 'Status', 'Address'])
merge_df

Zipcode  Population  Median Age  Household Income  Poverty Rate  \
10      08540     47316.0        37.5          125439.0      4.161383   
120     10001     21966.0        34.7           81671.0     15.364654   
121     10002     82191.0        39.8           33218.0     28.404570   
129     10011     52167.0        39.7          104238.0      8.394196   
139     10022     29618.0        45.3          109019.0      4.449997   
...       ...         ...         ...               ...           ...   
31386   91789     42609.0        42.5           91623.0      5.745265   
31387   91789     42609.0        42.5           91623.0      5.745265   
31478   92119     22965.0        43.1           67616.0      7.132593   
31815   78577     72047.0        28.6           32054.0     35.887684   
32871   96734     53068.0        34.7           89016.0      6.708374   

                Member Level Expiration Date       City       State  
10         Family Membership         4/30/21  Princeton  New Jersey  
120          Dual Membership        11/30/21   New York    New York  
121          Dual Membership         2/28/21   New York    New York  
129          Dual Membership        12/31/20   New York    New York  
139          Dual Membership         4/30/21   New York    New York  
...                      ...             ...        ...         ...  
31386        Dual Membership        11/30/21     Walnut  California  
31387        Dual Membership        11/30/21     Walnut  California  
31478  Individual Membership         3/31/21  San Diego  California  
31815      Family Membership         3/31/21      Pharr       Texas  
32871  Individual Membership         6/30/21     Kailua      Hawaii  

[1321 rows x 9 columns]

In [18]:
# Create database connection
import getpass

In [19]:
pwd_text=getpass.getpass('Enter password')

Enter password········


In [20]:
connection_string = f"postgres:{pwd_text}@localhost:5432/member_db"
engine = create_engine(f'postgresql://{connection_string}')

In [21]:
merge_df.to_sql(name='member', con=engine, if_exists='append', index=True)

In [22]:
# Check for table
engine.table_names()

['member']

In [23]:
# Confirm that data has been addedt to SQL by querying member merged file

pd.read_sql_query('select * from member', con=engine).head()

index Zipcode  Population  Median Age  Household Income  Poverty Rate  \
0     10   08540     47316.0        37.5          125439.0      4.161383   
1    120   10001     21966.0        34.7           81671.0     15.364654   
2    121   10002     82191.0        39.8           33218.0     28.404570   
3    129   10011     52167.0        39.7          104238.0      8.394196   
4    139   10022     29618.0        45.3          109019.0      4.449997   

        Member Level Expiration Date       City       State  
0  Family Membership         4/30/21  Princeton  New Jersey  
1    Dual Membership        11/30/21   New York    New York  
2    Dual Membership         2/28/21   New York    New York  
3    Dual Membership        12/31/20   New York    New York  
4    Dual Membership         4/30/21   New York    New York